In [4]:
from braintrust import init_logger
api_key = "sk-XNEbmBmj9uaKKTZN7QFdHOhrSZ1RyMLJqDoSW20WEvCax4TH"


logger = init_logger(project="peblV0", api_key=api_key)

In [5]:
import pandas as pd 

df = pd.read_csv("selected_conversations_with_topics_embedded_clustered.csv")

In [6]:
df.head()

Model                                       Conversation  \
0          gpt-4-0314  defaultdict(<class 'dict'>, {101001: {'user': ...   
1          gpt-4-0314  defaultdict(<class 'dict'>, {101004: {'user': ...   
2          gpt-4-0314  defaultdict(<class 'dict'>, {101008: {'user': ...   
3          gpt-4-0314  defaultdict(<class 'dict'>, {101012: {'user': ...   
4  gpt-3.5-turbo-0301  defaultdict(<class 'dict'>, {101015: {'user': ...   

  Language  Toxic         State        Country  Hour of Day  \
0  English  False         Texas  United States            0   
1  English  False  Mecca Region   Saudi Arabia            0   
2  English  False         Texas  United States            0   
3  English  False         Texas  United States            0   
4  English  False          Giza          Egypt            0   

                                     Topic_Embedding  \
0  [0.030988598242402077, -0.021997744217514992, ...   
1  [0.003948386758565903, 0.026730645447969437, -...   
2  [0.02941070683300495, -0.002898014383390546, -...   
3  [0.019601350650191307, -0.0199440885335207, -0...   
4  [-0.028554974123835564, -0.044307924807071686,...   

                                               Topic  L0_cluster_id  ...  \
0  The user requested a personalized reality-shif...             20  ...   
1  The user asked about the highest risk factor f...             18  ...   
2  The user asked for a personalized reality-shif...             20  ...   
3  The user asked for help choosing a reality-shi...             20  ...   
4  The user asked the assistant to write terms an...             42  ...   

                              L0_cluster_description  \
0  This cluster represents user requests for pers...   
1  This cluster represents medical consultations ...   
2  This cluster represents user requests for pers...   
3  This cluster represents user requests for pers...   
4  This cluster represents user attempts to solic...   

                    L0_cluster_description_embedding L1_cluster_id  \
0  [0.026203561574220657, 0.006107382941991091, -...             8   
1  [0.017507076263427734, 0.041330303996801376, -...            15   
2  [0.026203561574220657, 0.006107382941991091, -...             8   
3  [0.026203561574220657, 0.006107382941991091, -...             8   
4  [-0.0014729095855727792, -0.005219198763370514...             1   

                 L1_cluster_label  \
0  Fictional Character Narratives   
1         Medical Risk Assessment   
2  Fictional Character Narratives   
3  Fictional Character Narratives   
4   AI Assistant Boundary Testing   

                              L1_cluster_description  \
0  This cluster represents user requests focused ...   
1  This cluster encompasses healthcare consultati...   
2  This cluster represents user requests focused ...   
3  This cluster represents user requests focused ...   
4  This cluster represents diverse user interacti...   

                    L1_cluster_description_embedding L2_cluster_id  \
0  [-0.005672162398695946, 0.005445275921374559, ...             1   
1  [0.010494120419025421, 0.039453305304050446, -...             2   
2  [-0.005672162398695946, 0.005445275921374559, ...             1   
3  [-0.005672162398695946, 0.005445275921374559, ...             1   
4  [-0.008321586064994335, -0.0033742745872586966...             2   

                  L2_cluster_label  \
0  Fictional Narrative Exploration   
1            AI Capability Testing   
2  Fictional Narrative Exploration   
3  Fictional Narrative Exploration   
4            AI Capability Testing   

                              L2_cluster_description  \
0  This cluster represents user-generated content...   
1  This cluster represents comprehensive user int...   
2  This cluster represents user-generated content...   
3  This cluster represents user-generated content...   
4  This cluster represents comprehensive user int...   

                    L2_cluster_description_embedding  
0  [-0.01923833228647709, 

In [7]:
import ast

def parse_conversation_to_pairs(raw_conversation):
    """
    Parse a conversation string/dict and extract user-assistant pairs.
    
    Args:
        raw_conversation: Can be a string (with or without defaultdict wrapper) or dict
        
    Returns:
        list of tuples: [(user, assistant), (user, assistant), ...]
        Returns empty list if parsing fails or no valid pairs found
    """
    conversation_dict = {}
    
    # Handle defaultdict wrapper
    if isinstance(raw_conversation, str) and raw_conversation.startswith("defaultdict"):
        start = raw_conversation.find("{")
        end = raw_conversation.rfind("}")
        if start != -1 and end != -1:
            dict_str = raw_conversation[start:end+1]
            try:
                conversation_dict = ast.literal_eval(dict_str)
            except Exception as e:
                print(f"Failed to parse dict from defaultdict string: {e}")
                return []
        else:
            return []
    # If not a defaultdict wrapper, try to eval string or use as-is
    elif isinstance(raw_conversation, str):
        try:
            conversation_dict = ast.literal_eval(raw_conversation)
        except Exception as e:
            print(f"Failed to parse conversation string: {e}")
            return []
    elif isinstance(raw_conversation, dict):
        conversation_dict = raw_conversation
    else:
        return []
    
    # Extract pairs from the conversation dict
    pairs = []
    if isinstance(conversation_dict, dict):
        # Sort turn IDs to maintain order
        for turn_id in sorted(conversation_dict.keys()):
            turn = conversation_dict[turn_id]
            if isinstance(turn, dict):
                user_msg = turn.get("user", "")
                assistant_msg = turn.get("assistant", "")
                # Only add pair if both user and assistant messages exist
                if user_msg and assistant_msg:
                    pairs.append((user_msg, assistant_msg))
                elif user_msg:
                    # Log if user message exists but assistant doesn't
                    print(f"Warning: Turn {turn_id} has user message but no assistant message")
                elif assistant_msg:
                    # Log if assistant message exists but user doesn't
                    print(f"Warning: Turn {turn_id} has assistant message but no user message")
    
    return pairs

# Apply the function to all conversations in the dataframe
print("Extracting conversation pairs...")
df['conversation_pairs'] = df['Conversation'].apply(parse_conversation_to_pairs)

# Validate and show statistics
print(f"\nTotal conversations processed: {len(df)}")
print(f"Conversations with pairs: {df['conversation_pairs'].apply(lambda x: len(x) > 0).sum()}")
print(f"Total pairs extracted: {df['conversation_pairs'].apply(len).sum()}")
print(f"Average pairs per conversation: {df['conversation_pairs'].apply(len).mean():.2f}")

# Show examples
print("\n--- Example 1: First conversation pairs ---")
if len(df) > 0 and len(df['conversation_pairs'].iloc[0]) > 0:
    pairs = df['conversation_pairs'].iloc[0]
    print(f"Number of pairs: {len(pairs)}")
    print(f"First pair: {pairs[0]}")
    if len(pairs) > 1:
        print(f"Second pair: {pairs[1]}")

print("\n--- Example 2: Conversation with most pairs ---")
max_pairs_idx = df['conversation_pairs'].apply(len).idxmax()
max_pairs = df['conversation_pairs'].iloc[max_pairs_idx]
print(f"Conversation index: {max_pairs_idx}")
print(f"Number of pairs: {len(max_pairs)}")
if len(max_pairs) > 0:
    print(f"First pair: {max_pairs[0]}")


Extracting conversation pairs...

Total conversations processed: 1000
Conversations with pairs: 1000
Total pairs extracted: 2679
Average pairs per conversation: 2.68

--- Example 1: First conversation pairs ---
Number of pairs: 1
First pair: ('Hey there! Are you familiar with reality shifting? So, I’m refining a foolproof method for reality shifting and want to pick a destination. Want to help me? I’m thinking something pretty personalized. There are a few things that are required of my destination. 1. The quest. I have to have a clear overarching goal in my reality, and don’t make it too crazy. It should be more along the lines of “save the president’s daughter” or “escape this weird wacky sinister place” NOT “get an artifact that literally controls reality”. Seriously, don’t make me fetch an artifact, or fetch anything. Instead, make me DO something. 2. Babes. I need pretty girls. 3. The entry. I need to get to lose consciousness in order to begin my journey in my desired reality, pr

In [11]:
conversation_pairs = df['conversation_pairs'].iloc[0]

In [10]:
len(pairs)

1

In [8]:
print(f"user: {pairs[0][0]}")
print(f"assistant: {pairs[0][1]}")

user: Hey there! Are you familiar with reality shifting? So, I’m refining a foolproof method for reality shifting and want to pick a destination. Want to help me? I’m thinking something pretty personalized. There are a few things that are required of my destination. 1. The quest. I have to have a clear overarching goal in my reality, and don’t make it too crazy. It should be more along the lines of “save the president’s daughter” or “escape this weird wacky sinister place” NOT “get an artifact that literally controls reality”. Seriously, don’t make me fetch an artifact, or fetch anything. Instead, make me DO something. 2. Babes. I need pretty girls. 3. The entry. I need to get to lose consciousness in order to begin my journey in my desired reality, preferably by having it knocked out by one of the aforementioned babes. 4. Action. It needs to be cool. 5. Unconsciousness. Myself and the babes need to pass out in this place, preferably by being knocked out in some way or fainting. And it

In [13]:
for conversation in df['conversation_pairs']:
    for trace in conversation:
        logger.log(
            input=trace[0],
            output=trace[1],
            # Add other fields as needed
        )

In [12]:
for conversation in df['conversation_pairs']:
    for trace in conversation:
        print(trace)

('Hey there! Are you familiar with reality shifting? So, I’m refining a foolproof method for reality shifting and want to pick a destination. Want to help me? I’m thinking something pretty personalized. There are a few things that are required of my destination. 1. The quest. I have to have a clear overarching goal in my reality, and don’t make it too crazy. It should be more along the lines of “save the president’s daughter” or “escape this weird wacky sinister place” NOT “get an artifact that literally controls reality”. Seriously, don’t make me fetch an artifact, or fetch anything. Instead, make me DO something. 2. Babes. I need pretty girls. 3. The entry. I need to get to lose consciousness in order to begin my journey in my desired reality, preferably by having it knocked out by one of the aforementioned babes. 4. Action. It needs to be cool. 5. Unconsciousness. Myself and the babes need to pass out in this place, preferably by being knocked out in some way or fainting. And it sho